In [ ]:
import pandas as pd
xls = pd.ExcelFile('Lecture29_data/titanic3.xls')
sheet_1 = xls.parse(0)

In [ ]:
sheet_1.columns

In [ ]:
print(type(sheet_1))

In [ ]:
sheet_1

In [ ]:
sheet_1.iloc[0]

In [ ]:
from collections import Counter
c = Counter('baracadabra')
print(c)
d = c.most_common(3)
print(d)

In [ ]:
counter = Counter(sheet_1["survived"].values)
print(counter)
print("survived:", counter[1])
print("survival rate:", counter[1]/(counter[0]+counter[1]))

In [ ]:
counter = Counter(sheet_1.loc[sheet_1["body"].notna(), "survived"].values)
print(counter)

In [ ]:
print(sheet_1.groupby('pclass')['survived'].mean())

In [ ]:
print(sheet_1.groupby('sex')['survived'].mean())

In [ ]:
print(sheet_1.groupby(["pclass","sex"])["survived"].mean())

In [ ]:
print(sheet_1.groupby(["age"])["survived"].mean())

In [ ]:
Counter(sheet_1["age"])

In [ ]:
print(sheet_1.shape)
sheet_1.count()

In [ ]:
criteria = sheet_1.count() == sheet_1.shape[0]

In [ ]:
print(criteria)

In [ ]:
df = sheet_1[criteria.index[criteria]]
df

In [ ]:
print(sheet_1.shape)
print(df.shape)

In [ ]:
from sklearn import preprocessing

In [ ]:
le = preprocessing.LabelEncoder()

In [ ]:
data = sheet_1[criteria.index[criteria]]
data.loc[0:data.shape[0],'sex'] = le.fit_transform(data.sex)

In [ ]:
data = data.drop(['name','ticket'],axis=1)

In [ ]:
data

In [ ]:
from sklearn import model_selection
X = data.drop(["survived"], axis=1).values
y = data["survived"].values
X_train, X_test, y_train, y_test = model_selection.train_test_split(X,y,test_size=0.2, shuffle=True)

In [ ]:
X_train

In [ ]:
from sklearn.linear_model import LogisticRegression

In [ ]:
logitreg = LogisticRegression(solver='liblinear')
fit = logitreg.fit(X_train, y_train)

In [ ]:
effect_size = pd.DataFrame(fit.coef_)
effect_size.columns = data.drop(["survived"], axis=1).columns
effect_size

In [ ]:
y_train_pred = fit.predict(X_train)
y_test_pred = fit.predict(X_test)

The predictions are already thesholded to be either 0 or 1

In [ ]:
print(y_test_pred)

In [ ]:
acc_train = sum(y_train_pred==y_train)/len(y_train)
acc_test = sum(y_test_pred==y_test)/len(y_test)
print(f"train accuracy: {acc_train:.3f}; \
test accuracy: {acc_test:.3f}")

To get probabilities from logistic regression, we need to call the following function

In [ ]:
y_test_prob = fit.predict_proba(X_test)

In [ ]:
y_test_prob

In [ ]:
y_test_prob[:,1]

### Receiver Operator Characteristic (ROC) curve

Often we don't want to set a single threshold but rather evaluate the model based on all thresholds. ROC is the a way to this.

At each threshold, it calculates two rates:

True Positive Rate = True Positives / (True Positives + False Negatives)

False Positive Rate = False Positives / (False Positives + True Negatives)

In [ ]:
from sklearn.metrics import roc_curve
from sklearn.metrics import roc_auc_score
from matplotlib import pyplot

# calculate AUC
probs = y_test_prob[:,1]
auc = roc_auc_score(y_test, probs)
print('AUC: %.3f' % auc)
pyplot.plot([0, 1], [0, 1], linestyle='--')
# plot the roc curve for the model
fpr, tpr, thresholds = roc_curve(y_test, probs)
pyplot.plot(fpr, tpr, marker='.')
pyplot.xlabel("False Positive Rate")
pyplot.ylabel("True Positive Rate")
pyplot.show()